In [11]:
# h5 file structure
import h5py

def print_h5_structure(file, indent=0):
    """
    Recursively prints the structure of an HDF5 file.
    
    :param file: An HDF5 file object or group.
    :param indent: Current indentation level (for nested groups).
    """
    if isinstance(file, h5py.File) or isinstance(file, h5py.Group):
        for key in file.keys():
            item = file[key]
            print('  ' * indent + '|-- ' + key)
            if isinstance(item, h5py.Group):
                print_h5_structure(item, indent + 1)
            elif isinstance(item, h5py.Dataset):
                print('  ' * (indent + 1) + f'(Dataset, shape: {item.shape}, dtype: {item.dtype})')
    else:
        raise TypeError("The provided object is neither an HDF5 File nor Group.")

# Open the HDF5 file
file_path = 'MomentArms_Trunk_PelvisSacrumExtension.anydata.h5'  # Replace with your HDF5 file path
with h5py.File(file_path, 'r') as h5_file:
    print_h5_structure(h5_file)


|-- Output
  |-- Abscissa
    |-- StateCountCurrent
      (Dataset, shape: (), dtype: int32)
    |-- StateCountData
      (Dataset, shape: (2,), dtype: int32)
    |-- t
      (Dataset, shape: (2,), dtype: float64)
  |-- AngularVelocity_output
    |-- Val
      (Dataset, shape: (2,), dtype: float64)
  |-- Ekin
    (Dataset, shape: (2,), dtype: float64)
  |-- Emech
    (Dataset, shape: (2,), dtype: float64)
  |-- Epot
    (Dataset, shape: (2,), dtype: float64)
  |-- InitialConditions
    |-- ErrorCount
      (Dataset, shape: (2,), dtype: float64)
    |-- ErrorCountStep
      (Dataset, shape: (2,), dtype: float64)
    |-- KinematicError
      (Dataset, shape: (2,), dtype: float64)
    |-- RunDuration
      (Dataset, shape: (2,), dtype: float64)
    |-- RunDurationCPU
      (Dataset, shape: (2,), dtype: float64)
    |-- RunDurationCPUThread
      (Dataset, shape: (2,), dtype: float64)
  |-- KinematicError
    (Dataset, shape: (2,), dtype: float64)
  |-- Kinematics
    |-- ErrorCount
      

Code to get the h5 file, put the muscle names in the 1st column, strength in the 2nd column, and LmtDots in the next columns.

In [33]:
# Single file

import h5py
import pandas as pd

def traverse_h5_group(group, path=''):
    data = []
    for key in group.keys():
        item = group[key]
        new_path = f"{path}.{key}" if path else key
        if isinstance(item, h5py.Group):
            data.extend(traverse_h5_group(item, new_path))
        elif isinstance(item, h5py.Dataset):
            if key == 'Strength':
                # Process muscle name by removing 'Strength' and adding ';' at the end
                muscle_name = new_path.replace('.Strength', '') + ';'
                
                # Get the first value of the Strength array
                strength_array = item[()]
                if strength_array.size > 0:
                    strength = strength_array[0]  # Take only the first value
                else:
                    strength = None  # Handle cases where the array might be empty
                
                # Check if there's an 'LmtDot' dataset in the same group
                lmt_dot_array = None
                if 'LmtDot' in group:
                    lmt_dot_array = group['LmtDot'][()]  # Get the array directly
                
                # Initialize a dictionary to hold the muscle data
                entry = {'MuscleName': muscle_name, 'Strength': strength}
                
                # Add LmtDot values as separate columns
                if lmt_dot_array is not None:
                    for i, lmt_dot in enumerate(lmt_dot_array):
                        entry[f'LmtDot_{i}'] = lmt_dot
                
                data.append(entry)

    return data

# Load the .h5 file
file_path = 'MomentArms_Trunk_PelvisSacrumExtension.anydata.h5'
with h5py.File(file_path, 'r') as h5_file:
    # Navigate to the specific group
    base_group = h5_file['Output']['_Main']['HumanModel']['BodyModel']['Trunk']['Muscles']
    # Traverse the group and collect data
    muscles_data = traverse_h5_group(base_group)

# Create a DataFrame
df = pd.DataFrame(muscles_data)

# Remove columns where all values are None
df.dropna(axis=1, how='all', inplace=True)

# Filter out rows where any LmtDot_* column is less than 1e-6 or Strength is None
lmt_dot_cols = [col for col in df.columns if col.startswith('LmtDot_')]
for col in lmt_dot_cols:
    df = df[df[col].apply(lambda x: x is not None and x >= 1e-6)]

# Save DataFrame to a CSV file (optional)
df.to_csv('moment_arm_data.csv', index=False)

# Display the DataFrame
print(df)


                                      MuscleName    Strength  LmtDot_0  \
21                  Left.ErectorSpinae.ILplL1CI;   97.203199  0.009884   
27                 Left.ErectorSpinae.ILptC12CI;  132.299404  0.000823   
374                 Left.ObliquusExternus.OEC_1;   70.202597  0.006926   
375                Left.ObliquusExternus.OEC_10;   70.201395  0.013476   
376                Left.ObliquusExternus.OEC_11;   70.199861  0.011287   
...                                          ...         ...       ...   
1015  Right.QuadratusLumborum.QLC12Median_CILat;   14.174969  0.003155   
1020         Right.QuadratusLumborum.QLL1_CILat;   14.174975  0.000202   
1031        Right.QuadratusLumborum.QLT12_CILat;   14.174863  0.002334   
1033                 Right.RectusAbdominis.RA_1;  148.498410  0.018802   
1034                 Right.RectusAbdominis.RA_2;  148.494621  0.018749   

      LmtDot_1  
21    0.011799  
27    0.010036  
374   0.005904  
375   0.013095  
376   0.011920  
...      

For all spine joints

In [4]:
# Excel includes strength, LmtDot

import os
import h5py
import pandas as pd

def traverse_h5_group(group, path=''):
    """
    Traverse an HDF5 group recursively and collect data for each muscle.

    :param group: h5py.Group
        The HDF5 group to traverse.
    :param path: str
        The path used for recursive traversal.
    :return: list
        A list of dictionaries containing muscle data.
    """
    data = []
    for key in group.keys():
        item = group[key]
        new_path = f"{path}.{key}" if path else key
        if isinstance(item, h5py.Group):
            data.extend(traverse_h5_group(item, new_path))
        elif isinstance(item, h5py.Dataset):
            if key == 'Strength':
                # Process muscle name by removing 'Strength' and adding ';' at the end
                muscle_name = new_path.replace('.Strength', '') + ';'
                
                # Get the first value of the Strength array
                strength_array = item[()]
                if strength_array.size > 0:
                    strength = strength_array[0]  # Take only the first value
                else:
                    strength = None  # Handle cases where the array might be empty
                
                # Check if there's an 'LmtDot' dataset in the same group
                lmt_dot_array = None
                if 'LmtDot' in group:
                    lmt_dot_array = group['LmtDot'][()]  # Get the array directly
                
                # Initialize a dictionary to hold the muscle data
                entry = {'MuscleName': muscle_name, 'Strength': strength}
                
                # Add LmtDot values as separate columns
                if lmt_dot_array is not None:
                    for i, lmt_dot in enumerate(lmt_dot_array):
                        entry[f'LmtDot_{i}'] = lmt_dot
                
                data.append(entry)

    return data

def process_h5_file(file_path):
    """
    Process an HDF5 file and return a DataFrame with muscle data.

    :param file_path: str
        Path to the HDF5 file.
    :return: pd.DataFrame
        DataFrame containing the processed muscle data.
    """
    with h5py.File(file_path, 'r') as h5_file:
        # Navigate to the specific group
        base_group = h5_file['Output']['_Main']['HumanModel']['BodyModel']['Trunk']['Muscles']
        # Traverse the group and collect data
        muscles_data = traverse_h5_group(base_group)

    # Create a DataFrame
    df = pd.DataFrame(muscles_data)

    # Remove columns where all values are None
    df.dropna(axis=1, how='all', inplace=True)

    # Filter out rows where any LmtDot_* column is less than 1e-6 or Strength is None
    lmt_dot_cols = [col for col in df.columns if col.startswith('LmtDot_')]
    for col in lmt_dot_cols:
        df = df[df[col].apply(lambda x: x is not None and abs(x) >= 1e-6)]

    return df

def process_all_h5_files(directory):
    """
    Process all HDF5 files in a directory and write results to an Excel file.

    :param directory: str
        The directory to search for HDF5 files.
    """
    # Create a Pandas Excel writer using openpyxl as the engine
    with pd.ExcelWriter('muscle_data.xlsx', engine='openpyxl') as writer:
        # Iterate over all files in the directory
        for filename in os.listdir(directory):
            if filename.endswith('.h5'):
                # Get the full path to the file
                file_path = os.path.join(directory, filename)
                # Process the file
                df = process_h5_file(file_path)
                # Extract the sheet name from the filename
                sheet_name = os.path.splitext(filename)[0].split('_')[-1]
                # Write the DataFrame to a sheet in the Excel file
                df.to_excel(writer, sheet_name=sheet_name, index=False)
                print(f"Processed {filename} and written to sheet '{sheet_name}'")

# Specify the directory containing the .h5 files
directory_path = r'C:\Users\hs\Documents\AnyBody models\AMMR4-Beta\Application\Validation\EvaluateMomentArms\Output'

# Process all HDF5 files in the specified directory
process_all_h5_files(directory_path)


Processed MomentArms_Trunk_L1L2Extension.anydata.h5 and written to sheet 'L1L2Extension.anydata'
Processed MomentArms_Trunk_L2L3Extension.anydata.h5 and written to sheet 'L2L3Extension.anydata'
Processed MomentArms_Trunk_L3L4Extension.anydata.h5 and written to sheet 'L3L4Extension.anydata'
Processed MomentArms_Trunk_L4L5Extension.anydata.h5 and written to sheet 'L4L5Extension.anydata'
Processed MomentArms_Trunk_L5SacrumExtension.anydata.h5 and written to sheet 'L5SacrumExtension.anydata'
Processed MomentArms_Trunk_PelvisSacrumExtension.anydata.h5 and written to sheet 'PelvisSacrumExtension.anydata'
Processed MomentArms_Trunk_T12L1Extension.anydata.h5 and written to sheet 'T12L1Extension.anydata'


In [2]:
# Excel includes strength, MomentArm

import os
import h5py
import pandas as pd

# Specify the directory containing the .h5 files
directory_path = r'C:\Users\hs\Documents\AnyBody models\AMMR4-Beta\Application\Validation\EvaluateMomentArms\Output'

def traverse_h5_group(group, path='', angular_velocity=None):
    """
    Traverse an HDF5 group recursively and collect data for each muscle.

    :param group: h5py.Group
        The HDF5 group to traverse.
    :param path: str
        The path used for recursive traversal.
    :param angular_velocity: float
        Angular velocity to be used for moment arm calculation.
    :return: list
        A list of dictionaries containing muscle data.
    """
    data = []

    for key in group.keys():
        item = group[key]
        new_path = f"{path}.{key}" if path else key
        if isinstance(item, h5py.Group):
            data.extend(traverse_h5_group(item, new_path, angular_velocity))
        elif isinstance(item, h5py.Dataset):
            if key == 'Strength':
                # Process muscle name by removing 'Strength' and adding ';' at the end
                muscle_name = new_path.replace('.Strength', '') + ';'
                
                # Get the first value of the Strength array
                strength_array = item[()]
                if strength_array.size > 0:
                    strength = strength_array[0]  # Take only the first value
                else:
                    strength = None  # Handle cases where the array might be empty
                
                # Check if there's an 'LmtDot' dataset in the same group
                lmt_dot_array = None
                if 'LmtDot' in group:
                    lmt_dot_array = group['LmtDot'][()]  # Get the array directly

                # Initialize a dictionary to hold the muscle data
                entry = {'MuscleName': muscle_name, 'Strength': strength}
                
                # Add LmtDot values as separate columns if angular_velocity is available
                if lmt_dot_array is not None and angular_velocity is not None:
                    for i, lmt_dot in enumerate(lmt_dot_array):
                        if angular_velocity != 0:  # Prevent division by zero
                            entry[f'MomentArm_{i}'] = -lmt_dot / angular_velocity
                        else:
                            entry[f'MomentArm_{i}'] = None  # Handle division by zero case
                
                data.append(entry)

    return data

def get_angular_velocity(file_path):
    """
    Retrieve the angular velocity from the HDF5 file.

    :param file_path: str
        Path to the HDF5 file.
    :return: float or None
        Angular velocity if found, otherwise None.
    """
    try:
        with h5py.File(file_path, 'r') as h5_file:
            angular_velocity_path = 'Output/AngularVelocity_output/Val'
            # Ensure we are accessing a dataset, not a group
            if angular_velocity_path in h5_file:
                angular_velocity_dataset = h5_file[angular_velocity_path]
                # Access the dataset value, assuming it might be an array or a single value
                if isinstance(angular_velocity_dataset, h5py.Dataset):
                    # Retrieve the first value if it's an array
                    if angular_velocity_dataset.shape:
                        angular_velocity = angular_velocity_dataset[0]
                    else:
                        angular_velocity = angular_velocity_dataset[()]
                    return angular_velocity
                else:
                    print(f"'{angular_velocity_path}' is not a dataset.")
            else:
                print(f"Angular velocity path '{angular_velocity_path}' not found in {file_path}")

    except Exception as e:
        print(f"Error reading angular velocity from {file_path}: {e}")
    return None

def process_h5_file(file_path):
    """
    Process an HDF5 file and return a DataFrame with muscle data.

    :param file_path: str
        Path to the HDF5 file.
    :return: pd.DataFrame
        DataFrame containing the processed muscle data.
    """
    angular_velocity = get_angular_velocity(file_path)

    with h5py.File(file_path, 'r') as h5_file:
        # Navigate to the specific group
        try:
            base_group = h5_file['Output']['_Main']['HumanModel']['BodyModel']['Trunk']['Muscles']
        except KeyError as e:
            print(f"KeyError: {e}. The file structure is not as expected.")
            return pd.DataFrame()  # Return an empty DataFrame if structure is not as expected

        # Traverse the group and collect data
        muscles_data = traverse_h5_group(base_group, angular_velocity=angular_velocity)

    # Create a DataFrame
    df = pd.DataFrame(muscles_data)

    # Remove columns where all values are None
    df.dropna(axis=1, how='all', inplace=True)

    # Filter out rows where any MomentArm_* column is less than 1e-6 or Strength is None
    moment_arm_cols = [col for col in df.columns if col.startswith('MomentArm_')]
    for col in moment_arm_cols:
        df = df[df[col].apply(lambda x: x is not None and abs(x) >= 1e-6)]

    return df

def process_all_h5_files(directory):
    """
    Process all HDF5 files in a directory and write results to an Excel file.

    :param directory: str
        The directory to search for HDF5 files.
    """
    # Create a Pandas Excel writer using openpyxl as the engine
    with pd.ExcelWriter('muscle_MomentArm.xlsx', engine='openpyxl') as writer:
        # Track if any data is written
        data_written = False

        # Iterate over all files in the directory
        for filename in os.listdir(directory):
            if filename.endswith('.h5'):
                # Get the full path to the file
                file_path = os.path.join(directory, filename)
                
                # Process the file
                df = process_h5_file(file_path)
                
                # Only write to Excel if the DataFrame is not empty
                if not df.empty:
                    # Extract the sheet name from the filename
                    sheet_name = os.path.splitext(filename)[0].split('_')[-1]
                    # Write the DataFrame to a sheet in the Excel file
                    df.to_excel(writer, sheet_name=sheet_name, index=False)
                    data_written = True
                    print(f"Processed {filename} and written to sheet '{sheet_name}'")
                else:
                    print(f"No valid data found in {filename}, skipping.")

        # Check if any data was written
        if not data_written:
            print("No data was written to the Excel file. Check the input files and directory.")

# Process all HDF5 files in the specified directory
process_all_h5_files(directory_path)


Processed MomentArms_Trunk_C1C0Extension.anydata.h5 and written to sheet 'C1C0Extension.anydata'
Processed MomentArms_Trunk_C2C1AxialRotation.anydata.h5 and written to sheet 'C2C1AxialRotation.anydata'
Processed MomentArms_Trunk_C3C2AxialRotation.anydata.h5 and written to sheet 'C3C2AxialRotation.anydata'
Processed MomentArms_Trunk_C3C2Extension.anydata.h5 and written to sheet 'C3C2Extension.anydata'
Processed MomentArms_Trunk_C3C2LateralBending.anydata.h5 and written to sheet 'C3C2LateralBending.anydata'
Processed MomentArms_Trunk_C4C3AxialRotation.anydata.h5 and written to sheet 'C4C3AxialRotation.anydata'
Processed MomentArms_Trunk_C4C3Extension.anydata.h5 and written to sheet 'C4C3Extension.anydata'
Processed MomentArms_Trunk_C4C3LateralBending.anydata.h5 and written to sheet 'C4C3LateralBending.anydata'
Processed MomentArms_Trunk_C5C4AxialRotation.anydata.h5 and written to sheet 'C5C4AxialRotation.anydata'
Processed MomentArms_Trunk_C5C4Extension.anydata.h5 and written to sheet 'C

c:\Users\hs\mambaforge\envs\notebook\Lib\site-packages\openpyxl\workbook\child.py:99: UserWarning: Title is more than 31 characters. Some applications may not be able to read the file
  warnings.warn("Title is more than 31 characters. Some applications may not be able to read the file")


Processed MomentArms_Trunk_PelvisSacrumAxialRotation.anydata.h5 and written to sheet 'PelvisSacrumAxialRotation.anydata'
Processed MomentArms_Trunk_PelvisSacrumExtension.anydata.h5 and written to sheet 'PelvisSacrumExtension.anydata'


c:\Users\hs\mambaforge\envs\notebook\Lib\site-packages\openpyxl\workbook\child.py:99: UserWarning: Title is more than 31 characters. Some applications may not be able to read the file
  warnings.warn("Title is more than 31 characters. Some applications may not be able to read the file")


Processed MomentArms_Trunk_PelvisSacrumLateralBending.anydata.h5 and written to sheet 'PelvisSacrumLateralBending.anydata'
Processed MomentArms_Trunk_T10T11AxialRotation.anydata.h5 and written to sheet 'T10T11AxialRotation.anydata'
Processed MomentArms_Trunk_T10T11Extension.anydata.h5 and written to sheet 'T10T11Extension.anydata'
Processed MomentArms_Trunk_T10T11LateralBending.anydata.h5 and written to sheet 'T10T11LateralBending.anydata'
Processed MomentArms_Trunk_T11T12AxialRotation.anydata.h5 and written to sheet 'T11T12AxialRotation.anydata'
Processed MomentArms_Trunk_T11T12Extension.anydata.h5 and written to sheet 'T11T12Extension.anydata'
Processed MomentArms_Trunk_T11T12LateralBending.anydata.h5 and written to sheet 'T11T12LateralBending.anydata'
Processed MomentArms_Trunk_T12L1AxialRotation.anydata.h5 and written to sheet 'T12L1AxialRotation.anydata'
Processed MomentArms_Trunk_T12L1Extension.anydata.h5 and written to sheet 'T12L1Extension.anydata'
Processed MomentArms_Trunk_T1

In [14]:
# Excel includes strength, LmtDot, MomentArm


import os
import h5py
import pandas as pd

def traverse_h5_group(group, path=''):
    """
    Traverse an HDF5 group recursively and collect data for each muscle.

    :param group: h5py.Group
        The HDF5 group to traverse.
    :param path: str
        The path used for recursive traversal.
    :return: list
        A list of dictionaries containing muscle data.
    """
    data = []
    for key in group.keys():
        item = group[key]
        new_path = f"{path}.{key}" if path else key
        if isinstance(item, h5py.Group):
            data.extend(traverse_h5_group(item, new_path))
        elif isinstance(item, h5py.Dataset):
            if key == 'Strength':
                # Process muscle name by removing 'Strength' and adding ';' at the end
                muscle_name = new_path.replace('.Strength', '') + ';'
                
                # Get the first value of the Strength array
                strength_array = item[()]
                if strength_array.size > 0:
                    strength = strength_array[0]  # Take only the first value
                else:
                    strength = None  # Handle cases where the array might be empty
                
                # Check if there's an 'LmtDot' dataset in the same group
                lmt_dot_array = None
                if 'LmtDot' in group:
                    lmt_dot_array = group['LmtDot'][()]  # Get the array directly
                
                # Initialize a dictionary to hold the muscle data
                entry = {'MuscleName': muscle_name, 'Strength': strength}
                
                # Add LmtDot values as separate columns
                if lmt_dot_array is not None:
                    for i, lmt_dot in enumerate(lmt_dot_array):
                        entry[f'LmtDot_{i}'] = lmt_dot
                
                data.append(entry)

    return data

def process_h5_file(file_path):
    """
    Process an HDF5 file and return a DataFrame with muscle data.

    :param file_path: str
        Path to the HDF5 file.
    :return: pd.DataFrame
        DataFrame containing the processed muscle data.
    """
    with h5py.File(file_path, 'r') as h5_file:
        # Navigate to the specific group
        base_group = h5_file['Output']['_Main']['HumanModel']['BodyModel']['Trunk']['Muscles']
        # Traverse the group and collect data
        muscles_data = traverse_h5_group(base_group)

        # Extract AngularVelocity dataset
        angular_velocity_path = 'Output/AngularVelocity_output/Val'
        angular_velocity_array = h5_file[angular_velocity_path][()]

    # Create a DataFrame
    df = pd.DataFrame(muscles_data)

    # Remove columns where all values are None
    df.dropna(axis=1, how='all', inplace=True)

    # Filter out rows where any LmtDot_* column is less than 1e-6 or Strength is None
    lmt_dot_cols = [col for col in df.columns if col.startswith('LmtDot_')]
    for col in lmt_dot_cols:
        df = df[df[col].apply(lambda x: x is not None and abs(x) >= 1e-6)]

    # Add new columns for -LmtDot/AngularVelocity
    for col in lmt_dot_cols:
        index = int(col.split('_')[-1])  # Extract the index from LmtDot_*
        if index < len(angular_velocity_array):
            angular_velocity = angular_velocity_array[index]
            df[f'Ratio_{index}'] = -df[col] / angular_velocity

    return df

def process_all_h5_files(directory):
    """
    Process all HDF5 files in a directory and write results to an Excel file.

    :param directory: str
        The directory to search for HDF5 files.
    """
    # Create a Pandas Excel writer using openpyxl as the engine
    with pd.ExcelWriter('muscle_LmtDot_MomentArm.xlsx', engine='openpyxl') as writer:
        # Iterate over all files in the directory
        for filename in os.listdir(directory):
            if filename.endswith('.h5'):
                # Get the full path to the file
                file_path = os.path.join(directory, filename)
                # Process the file
                df = process_h5_file(file_path)
                # Extract the sheet name from the filename
                sheet_name = os.path.splitext(filename)[0].split('_')[-1]
                # Write the DataFrame to a sheet in the Excel file
                df.to_excel(writer, sheet_name=sheet_name, index=False)
                print(f"Processed {filename} and written to sheet '{sheet_name}'")

# Specify the directory containing the .h5 files
directory_path = r'C:\Users\hs\Documents\AnyBody models\AMMR4-Beta\Application\Validation\EvaluateMomentArms\Output'

# Process all HDF5 files in the specified directory
process_all_h5_files(directory_path)


Processed MomentArms_Trunk_L1L2Extension.anydata.h5 and written to sheet 'L1L2Extension.anydata'
Processed MomentArms_Trunk_L2L3Extension.anydata.h5 and written to sheet 'L2L3Extension.anydata'
Processed MomentArms_Trunk_L3L4Extension.anydata.h5 and written to sheet 'L3L4Extension.anydata'
Processed MomentArms_Trunk_L4L5Extension.anydata.h5 and written to sheet 'L4L5Extension.anydata'
Processed MomentArms_Trunk_L5SacrumExtension.anydata.h5 and written to sheet 'L5SacrumExtension.anydata'
Processed MomentArms_Trunk_PelvisSacrumExtension.anydata.h5 and written to sheet 'PelvisSacrumExtension.anydata'
Processed MomentArms_Trunk_T12L1Extension.anydata.h5 and written to sheet 'T12L1Extension.anydata'
